In [1]:
import pandas as pd

from bokeh.plotting import figure, output_file, show
from bokeh.io import output_notebook
from bokeh.models import WheelZoomTool
import pandas as pd

from bokeh.layouts import column
from bokeh.plotting import figure, output_file, show
from bokeh.models import ColumnDataSource, CustomJS, Slider

In [24]:
# pulling tick data
df = pd.read_csv('https://raw.githubusercontent.com/algostrat/bokeh_candlestick_timeframe/50334c1a55d5aaf9a9df250ec450c4207c00fb25/may2020.csv',
                 parse_dates=['RateDateTime'],
                 index_col=['RateDateTime'])

timeframes = ['1min','5min','15min','30min','1h']

In [33]:
# How do I store the data in a columndatastore?

data = {} # dictionary of dataframes
data2 = {} # dictionary of dictionaries of lists
data3 = {} # dictionary lists for each column
tfs = timeframes
for tf in tfs:
    data[tf] =  df['RateBid'].resample(tf).ohlc()
    data[tf] = data[tf] 

    data2[tf] =  data[tf].reset_index().to_dict(orient='list') 
    data2[tf]['RateDateTime'] = [dobj.strftime('%Y-%m-%d %H:%M:%S') for dobj in data2[tf]['RateDateTime']]

    # create a flat table of time frame data
    for col in ['RateDateTime', 'open','high','low','close']:
        data3[(tf+'-'+col)] =  data2[tf][col]


In [36]:
tf = '15min'
data15 = data[tf] #15 min candles

inc = data15.close > data15.open
dec = data15.open > data15.close
w = pd.Timedelta(tf)*.75

TOOLS = "pan,wheel_zoom,box_zoom,reset,save"

p = figure(
    x_axis_type="datetime", 
    tools=TOOLS, plot_width=1000, 
    sizing_mode="stretch_width",
    output_backend="webgl"
)

 # experimenting with passing in different dictionary data1,2,3 here (only data3 works so far)
alldata = ColumnDataSource(data=data3)
source = ColumnDataSource(data=data15)

callback = CustomJS(
    args=dict(alldata=alldata,source=source),
    code=
        """
            const f = cb_obj.value;
            const data = alldata.data;
            console.log(data);
        """
    )

slider = Slider(start=1, end=(len(timeframes) -1) , value=1, step=1, title="Time frame")
slider.js_on_change('value', callback)

p.toolbar.active_scroll = p.select_one(WheelZoomTool)
p.segment(data15.index, data15.high, data15.index, data15.low, color="black")
p.vbar(data15.index[inc], w, data15.open[inc], data15.close[inc], fill_color="#D5E1DD", line_color="black")
p.vbar(data15.index[dec], w, data15.open[dec], data15.close[dec], fill_color="#F2583E", line_color="black")
p.toolbar.logo = None

layout = column( p, slider)

output_notebook()
# output_file("bokeh_candlestick.html")
show(layout)

Loading BokehJS ...